In [66]:
import pandas as pd
import csv
import re
import pickle
import numpy as np
import multiprocessing

from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer

from wordcloud import WordCloud
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split

import gensim
from gensim.models import Word2Vec, Phrases
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Activation, Dense, Dropout, Embedding, Flatten, Conv1D, MaxPooling1D, LSTM
from keras import utils
from keras.callbacks import ReduceLROnPlateau, EarlyStopping

In [2]:
DATASET = "data/train.tsv"

In [3]:
df = pd.read_csv(DATASET, sep='\t')
df = df.drop(columns = ["PhraseId", "SentenceId"])
df.head()

Phrase  Sentiment
0  A series of escapades demonstrating the adage ...          1
1  A series of escapades demonstrating the adage ...          2
2                                           A series          2
3                                                  A          2
4                                             series          2

In [6]:
TEXT_CLEANING_RE = "@\S+|https?:\S+|http?:\S|[^A-Za-z0-9]+"
STOP_WORDS = set(stopwords.words("english"))
lemmatizer = WordNetLemmatizer()

def preprocess(text):
    text = re.sub(TEXT_CLEANING_RE, ' ', str(text).lower()).strip()
    words = word_tokenize(text) # tokenized words
    
    filter_text = [w for w in words if not w in STOP_WORDS]
    
    for text in filter_text:
        text = lemmatizer.lemmatize(text)
    
    return " ".join(filter_text)

In [7]:
df.Phrase = df.Phrase.apply(lambda x: preprocess(x))
df.head()

Phrase  Sentiment
0  series escapades demonstrating adage good goos...          1
1    series escapades demonstrating adage good goose          2
2                                             series          2
3                                                             2
4                                             series          2

In [8]:
with open('df.pickle', 'wb') as handle:
    pickle.dump(df, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [36]:
with open('df.pickle', 'rb') as handle:
    df = pickle.load(handle)

## Creating Vocabulary

In [59]:
all_reviews = np.array([], dtype=str)
all_reviews = df["Phrase"].to_numpy()
print('Total number of reviews:', len(all_reviews))

Total number of reviews: 156060


In [60]:
for review in all_reviews:
    print(review)

series escapades demonstrating adage good goose also good gander occasionally amuses none amounts much story
series escapades demonstrating adage good goose
series

series
escapades demonstrating adage good goose

escapades demonstrating adage good goose
escapades
demonstrating adage good goose
demonstrating adage
demonstrating
adage

adage
good goose

good goose

good goose

good goose
good
goose

goose
goose
also good gander occasionally amuses none amounts much story
also good gander occasionally amuses none amounts much story
also
also
good gander occasionally amuses none amounts much story
gander occasionally amuses none amounts much story
gander occasionally amuses none amounts much story
gander
gander
gander

occasionally amuses none amounts much story




occasionally amuses none amounts much story
occasionally
amuses none amounts much story
amuses
none amounts much story

none amounts much story
none
amounts much story
amounts much story
amounts much story
amounts
much story



cooler
pg 13 rating
pg 13 rating
pg 13
rating
smart provocative drama nearly impossible gets skin man know evil monstrous lunatic
smart provocative drama nearly impossible gets skin man know evil monstrous lunatic
smart provocative drama nearly impossible
smart provocative drama nearly impossible
smart provocative drama
smart provocative drama
provocative drama
provocative drama
provocative
drama
nearly impossible
nearly impossible
nearly impossible
nearly
impossible

gets skin man know evil monstrous lunatic
gets skin man know evil monstrous lunatic
gets
skin man know evil monstrous lunatic

skin man know evil monstrous lunatic
skin
skin
man know evil monstrous lunatic
man know evil monstrous lunatic
man
man
know evil monstrous lunatic

know evil monstrous lunatic
know evil monstrous lunatic
know
evil monstrous lunatic
evil monstrous lunatic
evil monstrous lunatic
evil
monstrous lunatic
monstrous lunatic
monstrous
lunatic
like drive
like drive
like drive
like drive
drive
drive
many th

riveting
unlikely story sarah harrison
unlikely story sarah harrison
unlikely story
unlikely story
unlikely
sarah harrison
sarah harrison
sarah
sarah
harrison
winds revelatory narcissistic achieving honest insight relationships high concept films candy coat pat storylines precious circumstances beautiful stars
winds revelatory narcissistic achieving honest insight relationships high concept films candy coat pat storylines precious circumstances beautiful stars
winds
revelatory narcissistic achieving honest insight relationships high concept films candy coat pat storylines precious circumstances beautiful stars
revelatory narcissistic achieving honest insight relationships high concept films candy coat pat storylines precious circumstances beautiful stars
revelatory narcissistic
revelatory narcissistic
revelatory narcissistic
revelatory narcissistic
revelatory
revelatory
narcissistic
achieving honest insight relationships high concept films candy coat pat storylines precious circumstanc

kind lush enveloping movie experience
lush enveloping movie experience
lush enveloping movie experience
lush
enveloping movie experience
enveloping movie experience
enveloping
movie experience
rhapsodizes
rhapsodizes
rare capability soothe break heart single stroke
rare capability soothe break heart single stroke
rare capability soothe break heart single stroke
rare capability soothe break heart single stroke
rare
capability soothe break heart single stroke
capability
soothe break heart single stroke
soothe break heart single stroke
soothe break heart
soothe break
soothe
soothe
break
heart
heart
single stroke
single stroke
single stroke
single
stroke
eerily accurate depiction depression
eerily accurate depiction depression
eerily accurate depiction
eerily accurate
eerily
accurate
depiction
depression
depression
feature length film wears welcome tryingly title character
feature length film
feature length film
feature length film
feature length
wears welcome tryingly title character
wear

finally revel splendor
finally revel splendor
revel splendor
revel
splendor
splendor
splendor
well done supernatural thriller keen insights parapsychological phenomena soulful nuances grieving process
well done supernatural thriller keen insights parapsychological phenomena soulful nuances grieving process
well done supernatural thriller keen insights parapsychological phenomena soulful nuances
well done supernatural thriller keen insights
well done supernatural thriller
well done
supernatural thriller
supernatural
keen insights
keen insights
keen
insights
parapsychological phenomena soulful nuances
parapsychological phenomena soulful nuances
parapsychological phenomena
parapsychological phenomena
parapsychological
phenomena
soulful nuances
soulful nuances
soulful
nuances
grieving process
grieving process
grieving process
grieving
process
bond save us latest eccentric super wealthy megalomaniac bent world domination destruction
bond save us latest eccentric super wealthy megalomaniac b

...

sappy preachy one
sappy preachy one
sappy preachy one
preachy one
preachy one
many things solid acting movie crafting something promising mediocre screenplay one
many things solid acting movie crafting something promising mediocre screenplay one
many things solid acting movie
many things solid acting movie
many things solid acting movie
many things solid acting movie
many things
solid acting movie
solid acting movie
movie
movie
crafting something promising mediocre screenplay one
crafting something promising mediocre screenplay
crafting
something promising mediocre screenplay
promising mediocre screenplay
mediocre screenplay
mediocre screenplay
mediocre screenplay
one
cautionary tale folly superficiality endlessly superficial
cautionary tale folly superficiality
folly superficiality
folly superficiality
folly superficiality
superficiality

endlessly superficial
superficial
lot things n
lot things n
lot things n
lot things n
lot things n
lot things n
things n
things n
things
n
hoping wo

sheer dumbness
plot lrb one good idea rrb movie inescapable air sleaziness
plot lrb one good idea rrb movie inescapable air sleaziness
plot lrb one good idea rrb
plot lrb one good idea rrb
lrb one good idea rrb
one good idea rrb
one good idea
one good idea
one good idea
one good idea
movie inescapable air sleaziness
movie inescapable air
inescapable air
sleaziness
sleaziness
get
get
classic spy action buddy movie entertaining enough worth look
classic spy action buddy movie entertaining enough worth look
classic spy action buddy movie
classic spy action buddy movie
classic spy action buddy movie
classic spy action buddy movie
classic spy action buddy movie
classic spy action buddy movie
spy action buddy movie
spy action
buddy movie
entertaining enough worth look
entertaining enough worth look
entertaining enough worth look
entertaining enough worth
enough worth
enough
priggish lethargically paced parable renewal
priggish
lethargically paced parable renewal
lethargically paced parable r

want lie dark room something cool brow
lie dark room something cool brow
lie dark room something cool brow
lie dark room something cool
lie
dark room something cool
dark room something cool
dark room
dark room
something cool
something cool
brow
brow
gets bogged hit miss topical humour getting truly good stuff
gets bogged hit miss topical humour getting truly good stuff
gets bogged hit miss topical humour getting truly good stuff
gets bogged hit miss topical humour
bogged hit miss topical humour
hit miss topical humour
hit miss topical humour
hit miss topical humour
topical humour
getting truly good stuff
getting truly good stuff
truly good stuff
truly good stuff
truly good stuff
truly good
bursts automatic gunfire story offers trenchant critique capitalism
bursts automatic gunfire
bursts automatic gunfire
automatic gunfire
automatic gunfire
automatic
story offers trenchant critique capitalism
story offers trenchant critique capitalism
offers trenchant critique capitalism
offers trencha

pretty much
pretty much


shot rich shadowy black white devils chronicles increasingly amused irony relationship reluctant captors befuddled captives
shot rich shadowy black white devils chronicles
rich shadowy black white devils chronicles
rich shadowy black white devils chronicles
rich shadowy black white
rich shadowy black white
shadowy black white
shadowy black white
devils chronicles
increasingly amused irony relationship reluctant captors befuddled captives
increasingly amused irony relationship reluctant captors befuddled captives
increasingly amused irony
increasingly amused irony
increasingly amused
relationship reluctant captors befuddled captives
relationship reluctant captors befuddled captives
relationship reluctant
reluctant
captors befuddled captives
captors befuddled captives
captors
captors
befuddled captives
captives
bond inspired
bond inspired
staggeringly dreadful romance
dreadful romance
dreadful romance
method almost never fails works superbly
method almost never 

presented universal appeal
universal appeal
universal appeal
french director turned nearly 21 2 hours unfocused excruciatingly tedious cinema half hour starts making water torture seem appealing
french director
turned nearly 21 2 hours unfocused excruciatingly tedious cinema half hour starts making water torture seem appealing
turned nearly 21 2 hours unfocused excruciatingly tedious cinema half hour starts making water torture seem appealing
turned nearly 21 2 hours unfocused excruciatingly tedious cinema half hour starts making water torture seem appealing
turned nearly 21 2 hours unfocused excruciatingly tedious cinema
nearly 21 2 hours unfocused excruciatingly tedious cinema
unfocused excruciatingly tedious cinema
unfocused excruciatingly tedious cinema
unfocused excruciatingly tedious
excruciatingly tedious
excruciatingly tedious
half hour starts making water torture seem appealing
half hour
half hour
half hour
starts making water torture seem appealing
making water torture seem a

In [67]:
cores = multiprocessing.cpu_count()
w2v_model = Word2Vec(min_count=20,
                     window=2,
                     size=300,
                     sample=6e-5, 
                     alpha=0.03, 
                     min_alpha=0.0007, 
                     negative=20,
                     workers=cores-1)

In [68]:
w2v_model.build_vocab(all_reviews, progress_per=10000)

In [71]:
w2v_model.train(all_reviews, total_examples=w2v_model.corpus_count, epochs=30, report_delay=1)

(5253318, 133670190)

In [75]:
w2v_model.init_sims(replace=True)

In [76]:
w2v_model.most_similar("forces")

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


KeyError: "word 'forces' not in vocabulary"

In [ ]:
w2v_model.wv.doesnt_match(['galaxy', 'starship', 'planet', 'dog'])

## Splitting Data

In [12]:
df_train, df_test = train_test_split(df, test_size=0.1, random_state=42)
print("TRAIN size:", len(df_train))
print("TEST size:", len(df_test))

TRAIN size: 140454
TEST size: 15606


In [231]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(df_train.Phrase)

vocab_size = len(tokenizer.word_index) + 1
print("Total words", vocab_size)

Total words 15130


In [233]:
x_train = pad_sequences(tokenizer.texts_to_sequences(df_train.Phrase), maxlen=300)
x_test = pad_sequences(tokenizer.texts_to_sequences(df_test.Phrase), maxlen=300)